Kütüphaneler eklenmesi

In [6]:
from datasets import load_dataset
import pandas as pd 
from pymongo import MongoClient
from transformers import BertTokenizer, BertForMaskedLM, DPRContextEncoderTokenizer,DPRContextEncoder;




Parquet dosyalarının dataframe olarak yüklenmesi(okuma yapabilmek için)

In [8]:
# Parquet dosyalarını DataFrame olarak yükleyin
train_df1 = pd.read_parquet('C:\\gitProjects\\yeni\\wikipedia-tr\\data\\train-00000-of-00002-ed6b025df7a1f653.parquet')
train_df2 = pd.read_parquet('C:\\gitProjects\\yeni\\wikipedia-tr\\data\\train-00001-of-00002-0aa63953f8b51c17.parquet')


In [9]:
# İki DataFrame'i birleştirin
merged_train = pd.concat([train_df1, train_df2], ignore_index=True)


In [10]:
# Örneğin %80 train, %20 test olarak ayırın
train_data = merged_train.sample(frac=0.8, random_state=42)
test_data = merged_train.drop(train_data.index)


In [11]:
import os

# Dosya yolları
train_dir = 'C:\\gitProjects\\yeni\\datasets\\train_Egitim'
test_dir = 'C:\\gitProjects\\yeni\\datasets\\test_Egitim'
train_file_path = os.path.join(train_dir, 'merged_train.parquet')
test_file_path = os.path.join(test_dir, 'merged_test.parquet')

# Dizinlerin var olup olmadığını kontrol etme, gerekirse oluşturma
os.makedirs(train_dir, exist_ok=True)
os.makedirs(test_dir, exist_ok=True)

# Veriyi .parquet formatında kaydetme
train_data.to_parquet(train_file_path)
test_data.to_parquet(test_file_path)

Dataframe deki bilgileri görme 

In [12]:
print(train_data.head())
print(test_data.head())

             id                                                url  \
515773  3525037  https://tr.wikipedia.org/wiki/P%C5%9F%C4%B1qo%...   
517811  3532700      https://tr.wikipedia.org/wiki/Craterolophinae   
436350  3203545           https://tr.wikipedia.org/wiki/Notocrabro   
223281  1765445    https://tr.wikipedia.org/wiki/Ibrahim%20Sissoko   
100272   575462        https://tr.wikipedia.org/wiki/Salah%20Cedid   

                  title                                               text  
515773    Pşıqo Ahecaqo  Pşıqo Ahecaqo (), Çerkes siyasetçi, askeri kom...  
517811  Craterolophinae  Craterolophinae, Depastridae familyasına bağlı...  
436350       Notocrabro  Notocrabro Crabronina oymağına bağlı bir cinst...  
223281  Ibrahim Sissoko  İbrahim Sissoko (d. 30 Kasım 1991), Fildişi Sa...  
100272      Salah Cedid  Salah Cedid (1926-1993) (Arapça: صلاح جديد) Su...  
    id                                             url        title  \
5   35       https://tr.wikipedia.org/wiki/Kar

MongoDb'ye bağlama ve bilgi çekme 

In [13]:
import pandas as pd
from pymongo import MongoClient

def get_mongodb(database_name='EgitimDatabase', train_collection_name='train', test_collection_name='test', host='localhost', port=27017):
    """
    MongoDB connection and collection selection for train and test collections.
    """
    client = MongoClient(f'mongodb://{host}:{port}/')
    
    # Veritabanını seçin
    db = client[database_name]
    
    # Train ve test koleksiyonlarını seçin
    train_collection = db[train_collection_name]
    test_collection = db[test_collection_name]
    
    return train_collection, test_collection

# Function to load dataset into MongoDB
def dataset_read(train_file_path,test_file_path):
    data_train = pd.read_parquet(train_file_path, columns=['id', 'url', 'title', 'text'])
    data_test = pd.read_parquet(test_file_path, columns=['id', 'url', 'title', 'text'])
    data_dict_train = data_train.to_dict("records")
    data_dict_test = data_test.to_dict("records")



    # Get the MongoDB collections
    train_collection, test_collection = get_mongodb(database_name='EgitimDatabase')

 

    # Insert data into MongoDB
    train_collection.insert_many(data_dict_train)
    test_collection.insert_many(data_dict_test)


    print(f" Veriler başarıyla {train_collection} MongoDb koleksiyonuna indirildi.")
    print(f" Veriler başarıyla {test_collection} MongoDb koleksiyonuna indirildi.")
    return train_collection,test_collection

# Train ve test datasetlerini MongoDB'ye yüklemek için fonksiyonu çağır
train_file_path = 'C:\\gitProjects\\yeni\\datasets\\train_Egitim\\merged_train.parquet'
test_file_path = 'C:\\gitProjects\\yeni\\datasets\\test_Egitim\\merged_test.parquet'

train_collection, test_collection = dataset_read(train_file_path, test_file_path)

 Veriler başarıyla Collection(Database(MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True), 'EgitimDatabase'), 'train') MongoDb koleksiyonuna indirildi.
 Veriler başarıyla Collection(Database(MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True), 'EgitimDatabase'), 'test') MongoDb koleksiyonuna indirildi.


In [ ]:
import pandas as pd
from pymongo import MongoClient,errors
from sklearn.feature_extraction.text import TfidfVectorizer
from sentence_transformers import SentenceTransformer

# MongoDB bağlantı ve koleksiyon seçimi için fonksiyon
def get_mongodb(database_name='EgitimDatabase', train_collection_name='train', test_collection_name='test', host='localhost', port=27017):
    client = MongoClient(f'mongodb://{host}:{port}/')
    db = client[database_name]
    train_collection = db[train_collection_name]
    test_collection = db[test_collection_name]
    return train_collection, test_collection

# Dataset'i MongoDB'ye yükleme fonksiyonu
def dataset_read(train_file_path, test_file_path):
    try:
        # MongoDB koleksiyonlarını al
        train_collection, test_collection = get_mongodb()

        # Eğer koleksiyonlar zaten doluysa, veri yüklemesi yapma
        if train_collection.estimated_document_count() > 0 or test_collection.estimated_document_count() > 0:
            print("Veriler zaten yüklendi, işlem yapılmadı.")
            return train_collection, test_collection

        # Datasetleri oku
        data_train = pd.read_parquet(train_file_path, columns=['id', 'url', 'title', 'text'])
        data_test = pd.read_parquet(test_file_path, columns=['id', 'url', 'title', 'text'])

        # Verileri MongoDB'ye yükle
        train_collection.insert_many(data_train.to_dict("records"))
        test_collection.insert_many(data_test.to_dict("records"))

        print(f"Veriler başarıyla {train_collection.name} koleksiyonuna yüklendi.")
        print(f"Veriler başarıyla {test_collection.name} koleksiyonuna yüklendi.")
    
    except errors.PyMongoError as e:
        print(f"Veri yükleme sırasında hata oluştu: {e}")

    return train_collection, test_collection



# Database sınıfı: Veritabanı bağlantıları ve verileri çekme işlevleri
class Database:
    @staticmethod
    def get_mongodb():
        return get_mongodb()

    @staticmethod
    def get_titles_and_texts():
        # MongoDB bağlantısı ve koleksiyonları al
        train_collection, _ = Database.get_mongodb()

        # Sorgu: Hem "title" hem de "text" alanı mevcut olan belgeler
        query = {"title": {"$exists": True}, "text": {"$exists": True}}

        # Belirtilen alanları seçiyoruz: "title", "text"
        cursor = train_collection.find(query, {"title": 1, "text": 1, "_id": 0})

        # Başlık ve metinleri doğru bir şekilde birleştiriyoruz
        documents = [{"title": doc['title'], "text": doc['text']} for doc in cursor]
        document_count = len(documents)
        return documents, document_count

# Train ve test datasetlerini MongoDB'ye yüklemek için fonksiyonu çağır
train_file_path = 'C:\\gitProjects\\yeni\\datasets\\train_Egitim\\merged_train.parquet'
test_file_path = 'C:\\gitProjects\\yeni\\datasets\\test_Egitim\\merged_test.parquet'

train_collection, test_collection = dataset_read(train_file_path, test_file_path)

# Veritabanından başlıklar ve metinler alınır
documents, document_count = Database.get_titles_and_texts()

# Sonuçların belirlenmesi
print(f"Başlık ve metin çiftleri: {documents}")
print(f"Toplam çift sayısı: {document_count}")


MongoDb üzerinden title ve text verilerinin çekilmesi 

In [ ]:
"""@staticmethod
    def get_input_titles():
        collection = Database.get_mongodb(collection_name='train')
        query = {"title": {"$exists": True}}
        cursor = collection.find(query, {"title": 1, "_id": 0})
        title_from_db = [doc['title'] for doc in cursor]

        return title_from_db"""

"""@staticmethod
    def get_input_texts():
        collection = Database.get_mongodb(collection_name='train')
        query = {"texts": {"$exists": True}}
        cursor = collection.find(query, {"texts": 1, "_id": 0})
        texts_from_db = [doc['texts'] for doc in cursor]
        return texts_from_db"""
    
    #bin tane veri çekerek csv dosyası olarak kaydetme 
   
    
"""@staticmethod
    def get_titles_and_texts(batch_size=1000):

        
        titles = Database.get_input_titles(batch_size=batch_size)
        texts = Database.get_input_texts(batch_size=batch_size )
        


    def test_queries():

        collection = Database.get_mongodb(collection_name='train')
        # Başlık sorgusu
        titles_cursor = collection.find({"title": {"$exists": True}}, {"title": 1, "_id": 0})
        titles = [doc['title'] for doc in titles_cursor]
        

        # Metin sorgusu
        texts_cursor = collection.find({"text": {"$exists": True}}, {"text": 1, "_id": 0})
        texts = [doc['text'] for doc in texts_cursor]
        
        # Başlık ve metinlerin eşleşmesini sağlamak için zip kullanarak birleştiriyoruz
        documents = [{"title": title, "text": text} for title, text in zip(titles, texts)]
        document_count = len(documents)
        return documents, document_count

Database.test_queries()

# Veritabanından başlıklar ve metinler alınır
documents, document_count = Database.get_titles_and_texts(batch_size=1000)

# Sonuçların belirlenmesi
print(f"Başlık ve metin çiftleri: {documents}")
print(f"Toplam çift sayısı: {document_count}")"""

Output'u vereceğimiz title ve textin kodu

In [8]:
from pymongo import MongoClient
import pandas as pd
from tqdm.auto import tqdm, trange

# Database bağlantıları ve verileri çekme işlevleri
class Database:
    @staticmethod
    def get_mongodb(database_name='EgitimDatabase', train_collection_name='train', test_collection_name='test', host='localhost', port=27017):
        client = MongoClient(f'mongodb://{host}:{port}/')
        db = client[database_name]
        train_collection = db[train_collection_name]
        test_collection = db[test_collection_name]
        return train_collection, test_collection

    def export_to_csv(batch_size=1000, output_file='combined_output.csv'):
        train_collection, _ = Database.get_mongodb()
        cursor = train_collection.find({}, {"title": 1, "text": 1, "_id": 0})
        cursor = cursor.batch_size(batch_size)  # Fix: Call batch_size on the cursor object

        # Verileri DataFrame'e dönüştürme
        df= pd.DataFrame(list(cursor))
        
        # title ve text sütunlarını birleştirme
        df['combined'] = df.apply(lambda row: f'**{row["title"]}** {row["text"]}', axis=1)
        
        #title,text and combined sütunlarını ayrı ayrı tutma
        #df2['title_only'] = df2['title']
        #df2['text_only'] = df2['text']
        #df['combined']= output_file

        # Sonuçları kontrol etme
        combined_text= df['combined'] 
          # Print the combined column directly
        
        print(combined_text.head())

        # Birleşmiş verileri CSV'ye kaydetme
        
        df.to_csv(output_file, index=False)
        
        print(f"Veriler combined_output.csv dosyasına başarıyla kaydedildi.")
        

# CSV dosyasını okuma ve birleştirme işlemi
Database.export_to_csv()

0    **Pşıqo Ahecaqo** Pşıqo Ahecaqo (), Çerkes siy...
1    **Craterolophinae** Craterolophinae, Depastrid...
2    **Notocrabro** Notocrabro Crabronina oymağına ...
3    **Ibrahim Sissoko** İbrahim Sissoko (d. 30 Kas...
4    **Salah Cedid** Salah Cedid (1926-1993) (Arapç...
Name: combined, dtype: object
Veriler combined_output.csv dosyasına başarıyla kaydedildi.


TF-IDF HESAPLAMA

In [13]:
#-------------------------tf-ıdf hesaplama
import re
import numpy as np
import pandas as pd
from nltk.stem import WordNetLemmatizer
from sklearn.feature_extraction.text import TfidfVectorizer
from nltk.corpus import stopwords as nltk_stopwords
from transformers import BertTokenizer, BertModel
import torch

# BERT Tokenizer ve Model'i yükleyin
tokenizer = BertTokenizer.from_pretrained('dbmdz/bert-base-turkish-cased')
model = BertModel.from_pretrained('dbmdz/bert-base-turkish-cased')


#-------------------------- burada turkish_stop_words'ü alıyoruz
def load_stop_words(file_path):
    """Stop words'leri dosyadan okuyarak bir liste oluşturur."""
    with open(file_path, 'r', encoding='utf-8') as file:
        stop_words = [line.strip() for line in file if line.strip()]
    return stop_words

# Türkçe stop words dosyasını yükleyin
stop_words_list = load_stop_words('turkish_stop_words.txt')

#gömülen kelimeleri k-means ile kümeleyebiliriz , benzerlik oranını hesaplamak için farklı algoritmalardan yararlanabiliriz.
def get_bert_embeddings(text):
    inputs = tokenizer(text, return_tensors='pt', truncation=True, padding=True)
    with torch.no_grad():
        outputs = model(**inputs)
    # Son katmandaki gömme (embedding) çıktısını alın
    return inputs['input_ids'],outputs.last_hidden_state

#--------------------------- textleri tokenize eden fonksiyon 
def get_token_embeddings(text):
    inputs = tokenizer(text, return_tensors='pt', truncation=True, padding=True)
    with torch.no_grad():
        outputs = model(**inputs)
    embeddings = outputs.last_hidden_state
    return embeddings

#------------------------------------ token verilerinin ortalaması (eşik değer için)
def average_embeddings(embeddings):
    # Token vektörlerinin ortalamasını alarak metin düzeyinde özet oluştur
    return torch.mean(embeddings, dim=1).squeeze()

#keywordsler çıkarmak için kullanacağım fonksiyon 
def extract_keywords_tfidf(corpus,stop_words_list):
    """TF-IDF ile anahtar kelimeleri çıkarır, stop words listesi ile birlikte kullanır."""
    vectorizer = TfidfVectorizer(stop_words=stop_words_list)
    X = vectorizer.fit_transform(corpus)
    feature_names = vectorizer.get_feature_names_out()
    scores = np.asarray(X.sum(axis=0)).flatten()
    keywords = {feature_names[i]: scores[i] for i in range(len(feature_names))}
    sorted_keywords = sorted(keywords.items(), key=lambda x: x[1], reverse=True)
    return sorted_keywords

#tokenleri kelimelere dönüştürür ve listeler 
def decode_tokens(input_ids):
    # Token ID'lerini kelimelere dönüştür
    tokens = tokenizer.convert_ids_to_tokens(input_ids.squeeze().tolist())
    return tokens

# Örnek metinler (buranın yerine combined_text kullanılacak)
texts = ["""Biyografi
İsim 
Pşıqo ismi Ahecaqo soy ismidir. Çerkeslerin "-qo" soneki ile biten hem soyadları hem de lakapları vardı. Bu ek Türkçe adlardaki "-oğlu" ekiyle eş anlamlıdır. Pşıqo Türkçe "Beyoğlu" anlamına gelen bir lakaptır.

Erken dönem 
Çerkesler tarihlerini yazmadıkları ve tüm bilgiler Rus kaynaklarından geldiği için Ahecaqo hakkında pek bir şey kaydedilmedi. 1777'de Çerkesya'nın Bjeduğ bölgesinde doğdu. Askerî eğitim ile büyütüldü.

Rus-Çerkes Savaşına Katılımı 
Birkaç kaynak, Ahecaqo'nun tüm Çerkesya'da saygı duyulan bir kişi olduğunu belirtir. En az 6.000 atlıdan oluşan kalıcı bir ordusu vardı ve çatışmalar sırasında müfrezesi 12.000 atlıya ulaşıyordu. Rus birliklerine karşı kazandığı zaferlerle ünlüydü. Askeri becerisinin yanı sıra yetenekli bir devlet adamıydı.

Ölüm 
1837 yılında Rus tarafına geçti ve bir yıl sonra hastalıktan öldü.

Kaynakça 

Çerkes soylular
1777 doğumlular
1838 yılında ölenler
Kafkas Savaşı'nda kişiler """]
         
    

    


#token ıd leri ve bert gömme vektörleri
for text in texts:
    input_ids,embeddings= get_bert_embeddings(text)
    
    # BERT gömme vektörlerini elde et
    #embeddings = [get_bert_embeddings(text) for text in texts]

    # Tokenları ve ortalama vektörleri al
    tokens = decode_tokens(input_ids)
    avg_embedding = average_embeddings(embeddings)
    print(f"Tokens: {tokens}")
    print(f"Average Embedding Shape: {avg_embedding.shape}")
    print(f"Average Embedding: {avg_embedding}")

# TF-IDF anahtar kelimelerini çıkar
keywords = extract_keywords_tfidf(texts,stop_words_list)
print("TF-IDF Keywords:", keywords)

# Gösterim
print("BERT Embeddings:")
for i, emb in enumerate(embeddings):
    print(f"Text {i+1} embedding shape: {emb.shape}")





Tokens: ['[CLS]', 'Biy', '##ografi', 'İsim', 'P', '##şı', '##q', '##o', 'ismi', 'Ah', '##ec', '##a', '##q', '##o', 'soy', 'ismi', '##dir', '.', 'Çerkes', '##lerin', '"', '-', 'q', '##o', '"', 'son', '##eki', 'ile', 'biten', 'hem', 'soya', '##d', '##ları', 'hem', 'de', 'lak', '##ap', '##ları', 'vardı', '.', 'Bu', 'ek', 'Türkçe', 'ad', '##lardaki', '"', '-', 'oğlu', '"', 'eki', '##yle', 'eş', 'anlamlı', '##dır', '.', 'P', '##şı', '##q', '##o', 'Türkçe', '"', 'Beyoğlu', '"', 'anlamına', 'gelen', 'bir', 'lak', '##ap', '##tır', '.', 'Erken', 'dönem', 'Çerkes', '##ler', 'tarihleri', '##ni', 'yazma', '##dıkları', 've', 'tüm', 'bilgiler', 'Rus', 'kaynaklarından', 'geldiği', 'için', 'Ah', '##ec', '##a', '##q', '##o', 'hakkında', 'pek', 'bir', 'şey', 'kayded', '##ilme', '##di', '.', '177', '##7', "'", 'de', 'Çerkes', '##ya', "'", 'nın', 'B', '##je', '##duğ', 'bölgesinde', 'doğdu', '.', 'Asker', '##î', 'eğitim', 'ile', 'büyüt', '##üldü', '.', 'Rus', '-', 'Çerkes', 'Savaşı', '##na', 'Katılım', '##

In [8]:
from sklearn.feature_extraction.text import TfidfVectorizer

def test_stop_words_effectiveness(corpus, stop_words_list):
    """Stop words listesinin etkisini test eder."""
    # İlk olarak, stop words olmadan TF-IDF hesaplayın
    vectorizer_no_stop_words = TfidfVectorizer()
    X_no_stop_words = vectorizer_no_stop_words.fit_transform(corpus)
    feature_names_no_stop_words = vectorizer_no_stop_words.get_feature_names_out()
    scores_no_stop_words = np.asarray(X_no_stop_words.sum(axis=0)).flatten()
    keywords_no_stop_words = {feature_names_no_stop_words[i]: scores_no_stop_words[i] for i in range(len(feature_names_no_stop_words))}
    sorted_keywords_no_stop_words = sorted(keywords_no_stop_words.items(), key=lambda x: x[1], reverse=True)

    # Şimdi, stop words ile TF-IDF hesaplayın
    vectorizer_with_stop_words = TfidfVectorizer(stop_words=stop_words_list)
    X_with_stop_words = vectorizer_with_stop_words.fit_transform(corpus)
    feature_names_with_stop_words = vectorizer_with_stop_words.get_feature_names_out()
    scores_with_stop_words = np.asarray(X_with_stop_words.sum(axis=0)).flatten()
    keywords_with_stop_words = {feature_names_with_stop_words[i]: scores_with_stop_words[i] for i in range(len(feature_names_with_stop_words))}
    sorted_keywords_with_stop_words = sorted(keywords_with_stop_words.items(), key=lambda x: x[1], reverse=True)
    
    # Stop words listesi etkisini gözlemleyin
    print("Keywords without stop words:")
    print(sorted_keywords_no_stop_words)
    
    print("\nKeywords with stop words:")
    print(sorted_keywords_with_stop_words)
    
    # Farklılıkları göster
    all_keywords_no_stop_words = set([kw[0] for kw in sorted_keywords_no_stop_words])
    all_keywords_with_stop_words = set([kw[0] for kw in sorted_keywords_with_stop_words])
    
    print("\nKeywords removed by stop words list:")
    print(all_keywords_no_stop_words - all_keywords_with_stop_words)
    
    print("\nNew keywords added by stop words list:")
    print(all_keywords_with_stop_words - all_keywords_no_stop_words)

# Test verisi ve stop words listesi kullanarak test edin
test_stop_words_effectiveness(texts, stop_words_list)


Keywords without stop words:
[('bir', np.float64(0.5)), ('bu', np.float64(0.5)), ('cümledir', np.float64(0.5)), ('örnek', np.float64(0.5)), ('anahtar', np.float64(0.3779644730092272)), ('kelimeleri', np.float64(0.3779644730092272)), ('kullanarak', np.float64(0.3779644730092272)), ('stop', np.float64(0.3779644730092272)), ('türkçe', np.float64(0.3779644730092272)), ('words', np.float64(0.3779644730092272)), ('çıkarıyoruz', np.float64(0.3779644730092272))]

Keywords with stop words:
[('cümledir', np.float64(0.7071067811865476)), ('örnek', np.float64(0.7071067811865476)), ('anahtar', np.float64(0.3779644730092272)), ('kelimeleri', np.float64(0.3779644730092272)), ('kullanarak', np.float64(0.3779644730092272)), ('stop', np.float64(0.3779644730092272)), ('türkçe', np.float64(0.3779644730092272)), ('words', np.float64(0.3779644730092272)), ('çıkarıyoruz', np.float64(0.3779644730092272))]

Keywords removed by stop words list:
{'bu', 'bir'}

New keywords added by stop words list:
set()


In [20]:
#---------------------------güncel en yeni 
from pymongo import MongoClient
from sklearn.feature_extraction.text import TfidfVectorizer
from textblob import TextBlob as tb
import numpy as np
import math
from tqdm.auto import tqdm, trange
import tensorflow as tf
import nltk
import re 
from nltk.stem import WordNetLemmatizer
from nltk.corpus import stopwords

turkish_stop_words = stopwords.words('turkish')

nltk.download('wordnet')
nltk.download('omw-1.4')
nltk.download('stopwords')


import matplotlib.pyplot as plt 

class Database:
    @staticmethod
    def get_mongodb():
        return 'mongodb://localhost:27017/', 'combined', 'combined_output'

    # Get input documents from MongoDB
    @staticmethod
    def get_input_documents(limit=1000):
        mongo_url, db_name, collection_name = Database.get_mongodb()
        client = MongoClient(mongo_url)
        db = client[db_name]
        collection = db[collection_name]
        cursor = collection.find().limit(limit)
        combined_text = [doc['text'] for doc in cursor]
        document_count = len(combined_text)
        return combined_text, document_count
    

    
    nltk.download('turkish_stop_words')
    data_without_stopwords = []
    for i in range(0, len(response)):
        doc = re.sub('[^a-zA-Z]', ' ', response[i])
        doc = doc.lower()
        doc = doc.split()
        doc = [lemmatizer.lemmatize(word) for word in doc if not word in set(stopwords)]
        doc = ' '.join(doc)
        data_without_stopwords.append(doc)

    #print ilk satır orjinal datasetteki
    print(data.response[0])

    # Calculate TF-IDF and get feature names
    @staticmethod
    def calculate_tfidf(documents, stop_words):
        vectorizer = TfidfVectorizer(stop_words=stop_words, max_features=10000,min_df=2)
        vectors = vectorizer.fit_transform(data_without_stopwords)
        tfidf_matrix = vectorizer.fit_transform(documents)
        feature_names = vectorizer.get_feature_names_out()
        return tfidf_matrix, feature_names

    # Extract keywords using TF-IDF
    def extract_keywords(tfidf_matrix, feature_names, top_n=10):
        keywords = {}
        for doc_idx, row in enumerate(tfidf_matrix):
            filtered_feature_names = [name for name in feature_names if name.lower() not in stop_words]
            scores = np.asarray(row.T.todense()).flatten()
            sorted_indices = np.argsort(scores)[::-1]
            top_features = sorted_indices[:top_n]
            doc_keywords = [(filtered_feature_names[idx], scores[idx]) for idx in top_features]
            keywords[f'document_{doc_idx+1}'] = doc_keywords
        return keywords
    
    #zip keywords and combined text 
    
    # Identify low TF-IDF words
    @staticmethod
    def identify_low_tfidf_words(tfidf_matrix, feature_names, threshold=0.001):
        avg_scores = np.mean(tfidf_matrix, axis=0).A1
        low_tfidf_words = [feature_names[i] for i, score in enumerate(avg_scores) if score < threshold]
        return low_tfidf_words
    
    # Update stop words with low TF-IDF words
    @staticmethod
    def update_stop_words(existing_stop_words, low_tfidf_words):
        updated_stop_words = set(existing_stop_words) | set(low_tfidf_words)
        return list(updated_stop_words)


#tf-ıdf ile döküman içerisinden kelime seçme 
#Term Frequency (TF): Bir kelimenin belli bir dökümanda tekrar etme değeri
#Inverse Document Frequency (IDF):bir kelimenin tüm dökümanlar arasındaki yaygınlığı Nadir bulunan kelimeler, daha yüksek IDF değerine sahip olur.
#tf-ıdf skoru ise bu ikisinin çarpımıdır.

    #buraya eşik değer belirlenmeli


turkish_stop_words = [
   'ah', 'ama', 'an', 'ancak', 'araba', 'aralar', 'aslında', 
    'b', 'başlayan', 'bağlı', 'bazı', 'belirli', 'ben', 'bence', 
    'birkaç', 'birlikte', 'bunu', 'burada', 'biten', 'biz', 
    'bu', 'buna', 'çünkü', 'da', 'de', 'demek', 'den', 'derken', 
    'değil', 'daha', 'dolayı', 'edilir', 'eğer', 'en', 'fakat', 
    'genellikle', 'gibi', 'hem', 'her', 'herhangi', 'hiç', 'ise', 
    'işte', 'itibaren', 'iyi', 'kadar', 'karşı', 'ki', 'kime', 
    'kısaca', 'mu', 'mü', 'nasıl', 'ne', 'neden', 'niye', 'o', 
    'olasılıkla', 'olabilir', 'oluşur', 'önce', 'şu', 'sadece', 
    'se', 'şey', 'şimdi', 'tabi', 'tüm', 've', 'ya', 'ya da', 
    'yanı', 'yani', 'yılında', 'yetenekli', 'yine'
]
# Get input documents
documents, document_count = Database.get_input_documents()

# Calculate TF-IDF and get feature names
tfidf_matrix, feature_names = Database.calculate_tfidf(documents, turkish_stop_words)

# Extract keywords
keywords = Database.extract_keywords(tfidf_matrix, feature_names, stop_words=turkish_stop_words)
print(keywords)

# Identify low TF-IDF words
low_tfidf_words = Database.identify_low_tfidf_words(tfidf_matrix, feature_names)
print(low_tfidf_words)

# Update stop words
updated_stop_words = Database.update_stop_words(turkish_stop_words, low_tfidf_words)
print(updated_stop_words) 

[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\info\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package omw-1.4 to
[nltk_data]     C:\Users\info\AppData\Roaming\nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\info\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


ValueError: empty vocabulary; perhaps the documents only contain stop words

In [15]:


"""class Tf:
    @staticmethod
    def tf(word, blob):
        return blob.words.count(word) / len(blob.words)

    @staticmethod
    def n_containing(word, bloblist):
        return sum(1 for blob in bloblist if word in blob.words)

    @staticmethod
    def idf(word, bloblist):
        return math.log(len(bloblist) / (1 + Tf.n_containing(word, bloblist)))

    @staticmethod
    def tfidf(word, blob, bloblist):
        return Tf.tf(word, blob) * Tf.idf(word, bloblist)

    @staticmethod
    def get_input_documents(limit=1000):
        return Database.get_input_documents(limit)"""





    """
    Her döküman için anahtar kelimeleri seç.
    :param tfidf_matrix: TF-IDF matris
    :param feature_names: TF-IDF özellik isimleri
    :param top_n: Her döküman için seçilecek anahtar kelime sayısı
    :return: Anahtar kelimeler ve skorlari
    """
    

#--------------------------------------------------------------- burada aldığımız  dökümanları listeliyoruz
# Dokümanları işleyerek TF-IDF hesaplama
#bloblist dökümanların bir listesi
"""bloblist = []
for i, blob in enumerate(bloblist):
    print("Top words in document {}".format(i + 1))
    scores = {word: Tf.tfidf(word, blob, bloblist) for word in blob.words} #dökümanların içerisinde bulunan kelimeleri alır.
    sorted_words = sorted(scores.items(), key=lambda x: x[1], reverse=True)
    for word, score in sorted_words[:3]:
        print("\tWord: {}, TF-IDF: {}".format(word, round(score, 5)))"""


# Dökümanları isimlendir
#named_documents = {f'döküman {i+1}': doc for i, doc in enumerate(combined_text)}

#features olarak top_keywordsleri belirleyerek metnin bu kelimelerin etrafında olması sağlanmalı  
def calculate_tfidf(documents, stop_words):
    vectorizer = TfidfVectorizer(stop_words=stop_words, max_features=10000)
    tfidf_matrix = vectorizer.fit_transform(documents)
    feature_names = vectorizer.get_feature_names_out()
    return tfidf_matrix, feature_names

#---------------------------------------------------------------------------------
#kelimelerin ortalama skorlarını hesaplama 
def identify_low_tfidf_words(tfidf_matrix, feature_names, threshold=0.001):
    # TF-IDF skorlarını toplayarak her kelimenin ortalama skorunu hesaplayın
    avg_scores = np.mean(tfidf_matrix, axis=0).A1
    low_tfidf_words = [feature_names[i] for i, score in enumerate(avg_scores) if score < threshold]
    return low_tfidf_words

#kelimelerin yeni geliştirilen eşik değere göre güncellenmesi 
def update_stop_words(existing_stop_words, low_tfidf_words):
    updated_stop_words = set(existing_stop_words) | set(low_tfidf_words)
    return list(updated_stop_words)


#bu kısım detaylandırılmalı 
def iterative_update(documents, initial_stop_words, iterations=5):
    stop_words = set(initial_stop_words)
    for _ in range(iterations):
        tfidf_matrix, feature_names = calculate_tfidf(documents, stop_words)
        low_tfidf_words = identify_low_tfidf_words(tfidf_matrix, feature_names)
        stop_words = update_stop_words(stop_words, low_tfidf_words)
    return list(stop_words)



def main ():

    
#anlam ilişkisini de kontrol edecek bir yapı oluşpturulacak title ile benzerlik kontrol ederek yüksek benzerlik içeren kelimler sıralnacak .

# Dökümanları liste olarak al
    named_documents, _ = Tf.get_input_documents(limit=1000)
    documents_list = [doc.get('text', '') if isinstance(doc, dict) else doc for doc in list(named_documents.values())]

    #başlangıç stop değerleriyle yeni olanları arasında değişim yapma 
    initial_stop_words = turkish_stop_words
    # Stop-words listesini iteratif olarak güncelleyin
    final_stop_words = iterative_update(documents_list, initial_stop_words)
    #tf-ıdf hesaplama
    tfidf_matrix, feature_names=calculate_tfidf(documents_list,final_stop_words)
    keywords=extract_keywords(tfidf_matrix,feature_names,top_n=10)

    

    print("Güncellenmiş Stop-Words Listesi:", final_stop_words)
    print("TF-IDF Matrix Shape:", tfidf_matrix.shape)
    print("Feature Names Sample:", feature_names[:10])  # İlk 10 feature adını gösterir

    return tfidf_matrix, feature_names,keywords

if __name__=="__main__":
    tfidf_matrix, feature_names,keywords= main()

    print("Anahtar Kelimler:")
    for doc, words in keywords.items():
        print(f"{doc}: {words}")
    

#---------------------------------------------------------
    """blobs = [tb(doc) for doc in documents_list]  # veya 'title' kullanarak başlıkları işleyebilirsiniz
    all_words = set(word for blob in blobs for word in blob.words)

    tfidf_scores = {}
    for word in all_words:
        tfidf_scores[word] = [Tf.tfidf(word, blob, blobs) for blob in blobs]

    print("TF-IDF Skorları:")
    for word, scores in tfidf_scores.items():
        print(f"Kelime: {word}, Skorlar: {scores}")"""


TypeError: unhashable type: 'set'

In [2]:
from pymongo import MongoClient
from sklearn.feature_extraction.text import TfidfVectorizer
from textblob import TextBlob as tb
import numpy as np
import math
import nltk 
import matplotlib.pyplot as plt 

class Database:
    @staticmethod
    def get_mongodb():
        return 'mongodb://localhost:27017/', 'EgitimDatabase', 'train'

#--------------------------------------------------------------------------
#combined_text eklenmeli 
    @staticmethod
    def get_input_documents(limit=3):
        mongo_url, db_name, collection_name = Database.get_mongodb()
        client = MongoClient(mongo_url)
        db = client[db_name]
        collection = db[collection_name]
        cursor = collection.find().limit(limit)
        combined_text = [doc for doc in cursor]
        document_count = len(combined_text)
        
        # Dökümanları isimlendir
        named_documents = {f'döküman {i+1}': doc for i, doc in enumerate(combined_text)}
        
        return named_documents, document_count


class Tf:
    @staticmethod
    def tf(word, blob):
        return blob.words.count(word) / len(blob.words)

    @staticmethod
    def n_containing(word, bloblist):
        return sum(1 for blob in bloblist if word in blob.words)

    @staticmethod
    def idf(word, bloblist):
        return math.log(len(bloblist) / (1 + Tf.n_containing(word, bloblist)))

    @staticmethod
    def tfidf(word, blob, bloblist):
        return Tf.tf(word, blob) * Tf.idf(word, bloblist)

    @staticmethod
    def get_input_documents(limit=3):
        return Database.get_input_documents(limit)

# Kullanım örneği
named_documents, document_count = Tf.get_input_documents(limit=1000)

#tf-ıdf ile döküman içerisinden kelime seçme 

def extract_keywords(tfidf_matrix, feature_names, top_n=10):
    """
    Her döküman için anahtar kelimeleri seç.
    :param tfidf_matrix: TF-IDF matris
    :param feature_names: TF-IDF özellik isimleri
    :param top_n: Her döküman için seçilecek anahtar kelime sayısı
    :return: Anahtar kelimeler ve skorlari
    """
    keywords = {}
    for doc_idx, row in enumerate(tfidf_matrix):
        # TF-IDF değerlerini ve özellik isimlerini al
        scores = np.asarray(row.T.todense()).flatten()
        sorted_indices = np.argsort(scores)[::-1]  # Skorları azalan sırada
        top_features = sorted_indices[:top_n]
        
        doc_keywords = [(feature_names[idx], scores[idx]) for idx in top_features]
        keywords[f'document_{doc_idx+1}'] = doc_keywords
    
    return keywords

# Dokümanları işleyerek TF-IDF hesaplama
#bloblist dökümanların bir listesi
bloblist = []
for i, blob in enumerate(bloblist):
    print("Top words in document {}".format(i + 1))
    scores = {word: Tf.tfidf(word, blob, bloblist) for word in blob.words} #dökümanların içerisinde bulunan kelimeleri alır.
    sorted_words = sorted(scores.items(), key=lambda x: x[1], reverse=True)
    for word, score in sorted_words[:3]:
        print("\tWord: {}, TF-IDF: {}".format(word, round(score, 5)))


#buraya eşik değer belirlenmeli
turkish_stop_words = [
    'ah', 'ama', 'an', 'ancak', 'araba', 'aralar', 'aslında', 
    'b', 'başlayan', 'bağlı', 'bazı', 'belirli', 'ben', 'bence', 
    'birkaç', 'birlikte', 'bunu', 'burada', 'biten', 'biz', 
    'bu', 'buna', 'çünkü', 'da', 'de', 'demek', 'den', 'derken', 
    'değil', 'daha', 'dolayı', 'edilir', 'eğer', 'en', 'fakat', 
    'genellikle', 'gibi', 'hem', 'her', 'herhangi', 'hiç', 'ise', 
    'işte', 'itibaren', 'iyi', 'kadar', 'karşı', 'ki', 'kime', 
    'kısaca', 'mu', 'mü', 'nasıl', 'ne', 'neden', 'niye', 'o', 
    'olasılıkla', 'olabilir', 'oluşur', 'önce', 'şu', 'sadece', 
    'se', 'şey', 'şimdi', 'tabi', 'tüm', 've', 'ya', 'ya da', 
    'yanı', 'yani', 'yılında', 'yetenekli', 'yine'
]

#features olarak top_keywordsleri belirleyerek metnin bu kelimelerin etrafında olması sağlanmalı  
def calculate_tfidf(combined_text, stop_words):
    vectorizer = TfidfVectorizer(stop_words=stop_words, max_features=10000)
    tfidf_matrix = vectorizer.fit_transform(combined_text)
    feature_names = vectorizer.get_feature_names_out()
    return tfidf_matrix, feature_names

#---------------------------------------------------------------------------------
#kelimelerin ortalama skorlarını hesaplama 
def identify_low_tfidf_words(tfidf_matrix, feature_names, threshold=0.001):
    # TF-IDF skorlarını toplayarak her kelimenin ortalama skorunu hesaplayın
    avg_scores = np.mean(tfidf_matrix, axis=0).A1
    low_tfidf_words = [feature_names[i] for i, score in enumerate(avg_scores) if score < threshold]
    return low_tfidf_words

#kelimelerin yeni geliştirilen eşik değere göre güncellenmesi 
def update_stop_words(existing_stop_words, low_tfidf_words):
    updated_stop_words = set(existing_stop_words) | set(low_tfidf_words)
    return list(updated_stop_words)


#bu kısım detaylandırılmalı 
def iterative_update(combined_text, initial_stop_words, iterations=5):
    stop_words = set(initial_stop_words)
    for _ in range(iterations):
        tfidf_matrix, feature_names = calculate_tfidf(combined_text, stop_words)
        low_tfidf_words = identify_low_tfidf_words(tfidf_matrix, feature_names)
        stop_words = update_stop_words(stop_words, low_tfidf_words)
    return list(stop_words)



def main ():

    
#anlam ilişkisini de kontrol edecek bir yapı oluşpturulacak title ile benzerlik kontrol ederek yüksek benzerlik içeren kelimler sıralnacak .

# Dökümanları liste olarak al
    documents_list = [doc.get('text', '') if isinstance(doc, dict) else doc for doc in list(named_documents.values())]

    #başlangıç stop değerleriyle yeni olanları arasında değişim yapma 
    initial_stop_words = turkish_stop_words
    # Stop-words listesini iteratif olarak güncelleyin
    final_stop_words = iterative_update(documents_list, initial_stop_words)
    #tf-ıdf hesaplama
    tfidf_matrix, feature_names=calculate_tfidf(documents_list,final_stop_words)

    

    print("Güncellenmiş Stop-Words Listesi:", final_stop_words)
    print("TF-IDF Matrix Shape:", tfidf_matrix.shape)
    print("Feature Names Sample:", feature_names[:10])  # İlk 10 feature adını gösterir

    return tfidf_matrix, feature_names,documents_list 

if __name__=="__main__":
    tfidf_matrix, feature_names,documents_list= main()


# Sonuçları yazdır
print("İsimlendirilmiş Dökümanlar:")
for name, doc in named_documents.items():
    print(f"{name}: {doc}")

    print("\nDökümanlar Listesi:")
    print(documents_list)

#---------------------------------------------------------
    blobs = [tb(doc) for doc in documents_list]  # veya 'title' kullanarak başlıkları işleyebilirsiniz
    all_words = set(word for blob in blobs for word in blob.words)

    tfidf_scores = {}
    for word in all_words:
        tfidf_scores[word] = [Tf.tfidf(word, blob, blobs) for blob in blobs]

    print("TF-IDF Skorları:")
    for word, scores in tfidf_scores.items():
        print(f"Kelime: {word}, Skorlar: {scores}")





#----------------------------------------------





#alternatif keywordleri belirleme 
#--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------
"""turkish_stop_words = set([
        'ad', 'adım', 'ah', 'ama', 'an', 'ancak', 'araba', 'aralar', 'aslında', 
     'b', 'bazı', 'belirli', 'ben', 'bence', 'bunu', 'burada', 'biz', 'bu', 'buna', 'çünkü', 
    'da', 'de', 'demek', 'den', 'derken', 'değil', 'daha', 'dolayı',  'edilir', 'eğer', 'en', 'fakat', 
    'genellikle', 'gibi', 'hem', 'her', 'herhangi', 'hiç', 'ise', 'işte', 'itibaren', 'iyi', 'kadar', 
    'karşı', 'ki', 'kime', 'kısaca', 'mu', 'mü', 'nasıl', 'ne', 'neden', 'niye', 'o', 'olabilir', 'oluşur', 
    'önce', 'şu', 'sadece', 'se', 'şey', 'şimdi', 'tabi', 'tüm', 've', 'ya', 'ya da', 'yani', 'yine'
])
def calculate_tfidf(documents):
    vectorizer = TfidfVectorizer(stop_words=turkish_stop_words, max_features=10000)  # max_features ile özellik sayısını sınırlıyoruz
    tfidf_matrix = vectorizer.fit_transform(documents)
    feature_names = vectorizer.get_feature_names_out()
    return tfidf_matrix, feature_names

#feature_names lerin belirlenmesi grekir 
tfidf_matrix, feature_names=calculate_tfidf(documents)



# En yüksek TF-IDF skorlarına sahip anahtar kelimeleri çıkarın
#sıkışık format kullanmarak tf-ıdf matrisini işleme 
def get_top_n_keywords_sparse(n=10):

    # TF-IDF hesaplayıcı oluşturun
    vectorizer = TfidfVectorizer()

    # Başlıklar ve metinler ile TF-IDF matrisini oluşturun
    texts = Database.get_input_texts()
    titles = Database.get_input_titles()
    

    #title ve text değerlerini alarak vektörleştirdik.
    tfidf_matrix = vectorizer.fit_transform(documents)

    # Özellik adlarını (kelimeleri) alın

    feature_names = vectorizer.get_feature_names_out()

    # TF-IDF sonuçlarını DataFrame'e dönüştürün
    df = pd.DataFrame(tfidf_matrix.toarray(), columns=feature_names)
    print(df)
    keywords = {}
    for i in range(tfidf_matrix.shape[0]):
        row = tfidf_matrix[i].toarray().flatten() #list yapısından çıkarma 
        sorted_indices = row.argsort()[::-1]  # Büyükten küçüğe sıralama
        top_indices = sorted_indices[:n]
        top_keywords = [feature_names[idx] for idx in top_indices]
        keywords[i] = top_keywords
    return keywords"""


InvalidParameterError: The 'stop_words' parameter of TfidfVectorizer must be a str among {'english'}, an instance of 'list' or None. Got {'o', 'den', 'an', 'şey', 'burada', 've', 'ah', 'ise', 'hiç', 'yine', 'biz', 'bu', 'da', 'genellikle', 'yılında', 'belirli', 'se', 'ne', 'kadar', 'neden', 'hem', 'aralar', 'yani', 'daha', 'araba', 'derken', 'dolayı', 'kısaca', 'karşı', 'niye', 'ki', 'bunu', 'buna', 'de', 'herhangi', 'önce', 'tabi', 'kime', 'biten', 'ben', 'ya', 'ya da', 'çünkü', 'mu', 'b', 'demek', 'fakat', 'şimdi', 'birlikte', 'her', 'bağlı', 'nasıl', 'şu', 'sadece', 'tüm', 'aslında', 'edilir', 'ama', 'bence', 'en', 'işte', 'gibi', 'ancak', 'birkaç', 'itibaren', 'mü', 'olabilir', 'bazı', 'oluşur', 'başlayan', 'yanı', 'olasılıkla', 'iyi', 'değil', 'eğer', 'yetenekli'} instead.

In [1]:

#---------------------------------------------------------------------------------------------------------------------------------
#transformers kütüphanesine ait generation fonksiyonu özellikleri ,PyTorch generate() is implemented in GenerationMixin. 


"""from transformers import GenerationConfig

# Download configuration from huggingface.co and cache.
generation_config = GenerationConfig.from_pretrained("openai-community/gpt2")

# E.g. config was saved using *save_pretrained('./test/saved_model/')*
generation_config.save_pretrained("./test/saved_model/")
generation_config = GenerationConfig.from_pretrained("./test/saved_model/")

# You can also specify configuration names to your generation configuration file
generation_config.save_pretrained("./test/saved_model/", config_file_name="my_configuration.json")
generation_config = GenerationConfig.from_pretrained("./test/saved_model/", "my_configuration.json")

# If you'd like to try a minor variation to an existing configuration, you can also pass generation
# arguments to `.from_pretrained()`. Be mindful that typos and unused arguments will be ignored
generation_config, unused_kwargs = GenerationConfig.from_pretrained(
    "openai-community/gpt2", top_k=1, foo=False, do_sample=True, return_unused_kwargs=True
)
generation_config.top_k

unused_kwargs
"""


#tf-ıdf hesaplama (anahtar kelimeler için) #Bir kelimenin TF IDF puanı ne kadar yüksekse, kelime bulunduğu belgeyle o kadar alakalıdır.

turkish_stop_words = set([
    'a', 'abide', 'abi', 'abla', 'ad', 'adım', 'ah', 'ama', 'an', 'ancak', 'araba', 'aralar', 'aslında', 
    'aşşağı', 'az', 'b', 'bazı', 'belirli', 'ben', 'bence', 'bunu', 'burada', 'biz', 'bu', 'buna', 'çünkü', 
    'da', 'de', 'demek', 'den', 'derken', 'değil', 'daha', 'dolayı', 'e', 'edilir', 'eğer', 'en', 'fakat', 
    'genellikle', 'gibi', 'hem', 'her', 'herhangi', 'hiç', 'i', 'ise', 'işte', 'itibaren', 'iyi', 'kadar', 
    'karşı', 'ki', 'kime', 'kısaca', 'mu', 'mü', 'nasıl', 'ne', 'neden', 'niye', 'o', 'olabilir', 'oluşur', 
    'önce', 'şu', 'sadece', 'sana', 'se', 'şey', 'şimdi', 'tabi', 'tüm', 've', 'ya', 'ya da', 'yani', 'yine'
])

# TF-IDF hesaplayıcı oluşturun ve Türkçe durak kelimelerini dahil edin
vectorizer = TfidfVectorizer(stop_words=turkish_stop_words)


"""IDF, derlemedeki belge sayısının,
incelenen anahtar kelimeyi içeren topluluktaki belge sayısına 
bölünmesiyle elde edilen algoritmadır. 
Yani ters belge sıklığı bir terimin önemini ölçer,
toplam belge sayısının, terimi içeren belge sayısına bölünmesiyle elde edilir.
külliyat yani incelenen tüm belgelerin adedi 10 ise ve test edilen anahtar kelime,
külliyattaki üç belgede görünüyorsa, bu durumda IDF değeri 0.52’dir (log (10/3))."""
#TF-IDF puanı; Naive Bayes ve Destek Vektör Makineleri gibi algoritmalara aktarılabilir. Böylece kelime sayısı gibi daha temel yöntemlerin sonuçları büyük ölçüde iyileştirilebilir.
#IDF = log ( Dokuman Sayısı / Terimin Geçtiği Dokuman Sayısı )
#dokuman sayısılarını almakla başlayacağız.
#  : titlelerın sayısı / terimler ise 

document_number=416434
"""Sonuç olarak TF IDF’nin, SEO’da pratik ve önemli bir kullanım alanına sahip olduğunu söylenebilir,
 özellikle yüksek kaliteli içeriğin optimize edilmesinde ve oluşturulmasında yararlıdır. 
 Ancak TF IDF, içerik optimizasyonu için tek başına kullanıldığında ciddi sınırlamalarla karşı karşıya kalır:"""

# TF-IDF hesaplayıcı oluşturun
vectorizer = TfidfVectorizer()

# Başlıklar ve metinler ile TF-IDF matrisini oluşturun
texts = Database.get_input_texts()
titles,title_count = Database.get_input_titles()
documents = titles + texts  # Başlıklar ve metinleri birleştir

#title ve text değerlerini alarak vektörleştirdik.
tfidf_matrix = vectorizer.fit_transform(documents)

# Özellik adlarını (kelimeleri) alın

feature_names = vectorizer.get_feature_names_out()

# TF-IDF sonuçlarını DataFrame'e dönüştürün
df = pd.DataFrame(tfidf_matrix.toarray(), columns=feature_names)


"""def get_top_n_keywords(df, n=10):
    keywords = {}
    for i, row in df.iterrows():
        sorted_row = row.sort_values(ascending=False)
        top_keywords = sorted_row.head(n).index
        keywords[i] = top_keywords.tolist()
    return keywords"""

# En yüksek TF-IDF skorlarına sahip anahtar kelimeleri çıkarın
#sıkışık format kullanmarak tf-ıdf matrisini işleme 
def get_top_n_keywords_sparse(n=10):

    # TF-IDF hesaplayıcı oluşturun
    vectorizer = TfidfVectorizer()

    # Başlıklar ve metinler ile TF-IDF matrisini oluşturun
    texts = Database.get_input_texts()
    titles = Database.get_input_titles()
    

    #title ve text değerlerini alarak vektörleştirdik.
    tfidf_matrix = vectorizer.fit_transform(documents)

    # Özellik adlarını (kelimeleri) alın

    feature_names = vectorizer.get_feature_names_out()

    # TF-IDF sonuçlarını DataFrame'e dönüştürün
    df = pd.DataFrame(tfidf_matrix.toarray(), columns=feature_names)
    print(df)
    keywords = {}
    for i in range(tfidf_matrix.shape[0]):
        row = tfidf_matrix[i].toarray().flatten() #list yapısından çıkarma 
        sorted_indices = row.argsort()[::-1]  # Büyükten küçüğe sıralama
        top_indices = sorted_indices[:n]
        top_keywords = [feature_names[idx] for idx in top_indices]
        keywords[i] = top_keywords
    return keywords


top_keywords = get_top_n_keywords_sparse(tfidf_matrix, feature_names)
print(top_keywords)
print(f"Başlıklar: {titles}")
print(f"Başlık sayısı: {title_count}")
print(f"Metinler: {texts}")
print(f"Metin sayısı: {len(texts)}")
print(f"Birleştirilmiş Belgeler: {documents[:5]}")  # İlk birkaç belgeyi kontrol etme

def calculate_tfidf(docs):
    vectorizer = TfidfVectorizer(stop_words=turkish_stop_words)
    tfidf_matrix = vectorizer.fit_transform(docs)
    feature_names = vectorizer.get_feature_names_out()
    return tfidf_matrix, feature_names

# İşlem için dökümanları parçalayarak kullanın
def process_documents_in_batches(docs, batch_size=1000, top_n=5):
    all_keywords = {}
    for start in range(0, len(docs), batch_size):
        end = min(start + batch_size, len(docs))
        batch_docs = docs[start:end]
        tfidf_matrix, feature_names = calculate_tfidf(batch_docs)
        batch_keywords = get_top_n_keywords_sparse(tfidf_matrix, feature_names, n=top_n)
        all_keywords.update(batch_keywords)
    return all_keywords

#buraya mango db üzerindeki tüm dökümanlar gelmewli 
keywords= process_documents_in_batches(documents,batch_size=1000,top_n=5)

documents = titles + texts  # Başlıklar ve metinleri birleştir
print(f"en yüksek tf-ıdf skoruna sahip anahtar kelimeler:{keywords}")


# Belgeleri TF-IDF matrisine dönüştürün
"""tfidf_matrix = vectorizer.fit_transform(documents)

# Özellik adlarını (kelimeleri) alın
feature_names = vectorizer.get_feature_names_out()

# TF-IDF sonuçlarını DataFrame'e dönüştürün
df = pd.DataFrame(tfidf_matrix.toarray(), columns=feature_names)

print(df)"""

#text ve title a göre keywords belirlenmesi

#------------------------------------------------------------------------------


#sbert ile alt başlıkların oluşturulması

#kümelenme ile alt başlıkların belirlenmesi 

#-------------------------------------------------------------------------------

#anahatar kelime ve alt başlıkların veri tabnaına eklnemesi 

NameError: name 'TfidfVectorizer' is not defined

In [ ]:
#benzerlik hesaplaması için kullanılacak 
from sentence_transformers import SentenceTransformer

Similarity Sentences 

In [ ]:
#prompt oluştururak generate etmek için hazırlık

Bert Modeliyle tokenizer atama

In [ ]:
tokenizer= BertTokenizer.from_pretrained('bert-base-uncased')
model=BertForMaskedLM.from_pretrained('bert-base-uncased')

"""BERT MODELİNİ AYARLAMA

input_file: Modelin işlem yapacağı giriş dosyasının yolunu belirtir. Bu dosya, metin verilerini içermelidir.
-----------------------------------------------------------------------------------------------------------------
output_file: Modelin çıktılarının kaydedileceği dosyanın yolunu belirtir.
------------------------------------------------------------------------------------------------------------------
layers: Hangi BERT katmanlarının kullanılacağını belirler. Örneğin, "-1,-2,-3,-4" son dört katmanı ifade eder.
----------------------------------------------------------------------------------------------------------------------
bert_config_file: Önceden eğitilmiş BERT modelinin yapılandırma dosyasının yolu. Bu dosya modelin mimarisini belirler.
--------------------------------------------------------------------------------------------------------------------------
max_seq_length: Giriş sekanslarının maksimum uzunluğu. Sekanslar bu uzunluktan uzunsa kesilir, kısa ise sıfır ile doldurulur.
--------------------------------------------------------------------------------------------------------------------------------
init_checkpoint: Başlangıç ağırlıkları. Genellikle önceden eğitilmiş bir BERT modelinin ağırlıkları buradan yüklenir.
----------------------------------------------------------------------------------------------------------------------------
vocab_file: BERT modelinin eğitildiği kelime dağarcığının (vocabulary) dosya yolu. Modelin kelime parçacıklarını tanıması için gereklidir.
--------------------------------------------------------------------------------------------------------------------------------------------------
do_lower_case: Giriş metinlerinin küçük harfe mi dönüştürüleceğini belirler. Küçük harfli model için True, büyük harfli model için False olmalıdır.
-----------------------------------------------------------------------------------------------------------------------------------------------------------
batch_size: Tahminler sırasında kullanılacak veri kümesi boyutu.
--------------------------------------------------------------------------------------------------------------------------------------
use_tpu: TPU (Tensor Processing Unit) kullanılıp kullanılmayacağını belirler. True ise TPU, False ise GPU/CPU kullanılır.
--------------------------------------------------------------------------------------------------------------------------------
master: TPU kullanılıyorsa, TPU'nun ana makinesinin adresi.
---------------------------------------------------------------------------------------------------------------------------------------
num_tpu_cores: TPU kullanılacaksa, toplam TPU çekirdek sayısını belirtir.
-----------------------------------------------------------------------------------------------------------------------------------------
use_one_hot_embeddings: TPUs'da genellikle True olarak ayarlanır çünkü bu, tf.one_hot fonksiyonunu kullanarak embedding lookup işlemlerini hızlandırır. GPU/CPU kullanılıyorsa False tercih edilir."""


t5 Modeli

In [ ]:
from transformers import pipeline
from dotenv import load_dotenv
import os 
# Load model directly
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM


#tokenizer ve modelin yüklenmesi
tokenizer = AutoTokenizer.from_pretrained("google/flan-t5-small")
model = AutoModelForSeq2SeqLM.from_pretrained("google/flan-t5-small")
prompt = "Write an article about Machine Learning in Healthcare focusing on Introduction to ML and Applications in Healthcare."
#api anahtarını çevresel değişken al
api_key= os.getenv('HUGGINGFACE_API_KEY')
#env dosyasını yükleme
load_dotenv()

#---------------------------------------------------------------------------------
if api_key is None:
    raise ValueError("Apı anahtarı .env dosyasında bulunamadı")

# Başlıkları oluştur
headers = {"Authorization": f"Bearer {api_key}"}

inputs=tokenizer(prompt, return_tensors="pt")
input_sequence = "[CLS] Machine Learning in Healthcare [SEP] Introduction to ML [SEP] Applications in Healthcare [SEP] machine learning, healthcare, AI [SEP]"
#deneme data parçası
data = {
    "title": "Machine Learning in Healthcare",
    "sub_headings": ["Introduction to ML", "Applications in Healthcare"],
    "keywords": ["machine learning", "healthcare", "AI"]
}

# Girdiyi oluşturma
prompt = (
    f"Title: {data['title']}\n"
    f"Sub-headings: {', '.join(data['sub_headings'])}\n"
    f"Keywords: {', '.join(data['keywords'])}\n"
    f"Content: {input_sequence}\n"
    "Please generate a detailed article based on the above information."
)

#metin üretimi 
output_sequences = model.generate(
    inputs['input_ids'],
    max_length=300,  # Üretilecek metnin maksimum uzunluğu
    min_length=150,  # Üretilecek metnin minimum uzunluğu
    num_return_sequences=1,  # Döndürülecek metin sayısı
    do_sample=True,  # Örneklemeye izin ver
    top_k=50,  # Top-k sampling kullan
    top_p=0.95,  # Top-p sampling kullan
    repetition_penalty=1.2,  # Anlamsız tekrarları önlemek için ceza
    eos_token_id=tokenizer.eos_token_id  # Tam cümlelerin oluşturulmasını sağla
)


# Üretilen metni token'lardan çözüp string'e çevir
generated_text = tokenizer.decode(output_sequences[0], skip_special_tokens=True)

print(generated_text)
